<a href="https://colab.research.google.com/github/XiaoLiang28/Datamanagement/blob/main/PS2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In this ps I want to explore the ethnic condition of students and teachers in school districts in Camden County. Research found that in while many schools have a high rate of Black and Hispanic students, the majority of teachers is White. I want to see if it is true in Camden County.

Dataset 1 from https://www.nj.gov/education/doedata/enr/ (2020-2021 Enrollment District Reported Data)

Dataset 2 from https://www.nj.gov/education/doedata/cs/index.shtml (2020-2021 Certificated Staff)

# Set Up

In [108]:
#---------------------------SETUP----------------------------------
#get useful libraries
import time, os, sys, re #basics
import zipfile, json, datetime, string   #string for annotating points in scatter
import numpy as np #basic math
from statistics import * #stats

import matplotlib.pyplot as plt #import pylab as plt #apparently discouraged now:
 #https://stackoverflow.com/questions/11469336/what-is-the-difference-between-pylab-and-pyplot
 #https://www.tutorialspoint.com/matplotlib/matplotlib_pylab_module.htm

import pandas as pd
import pandas_datareader as pdr
from pandas_datareader import wb
from pandas.io.formats.style import Styler
#s4 = Styler(df4, uuid_len=0, cell_ids=False)

import urllib  #weird, guess need to have os and pandas imported for this to work  %TODO/LATER ditch it, its weird anyway, just use wget/curl

from google.colab import files

#import webbrowser

import seaborn as sns

from google.colab import data_table
data_table.enable_dataframe_formatter() #this enables spreadsheet view upon calling dataframe (without() )

#many tricks how to extend notebook functionality
#https://coderzcolumn.com/tutorials/python/list-of-useful-magic-commands-in-jupyter-notebook-lab
#will display all output not just last command
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

#MAGICS and THEMES/STYLES: important! does affect not just shading/colors, but also fonts, spacing, etc
#(even if you only select default (v not selecting anything) [but does seem to work better if you do make explicit sleections])

###magics: https://ipython.readthedocs.io/en/stable/interactive/magics.html
#most essential setup for vis: it does affect vis! careful!! stick with inline, maybe notebook; others mostly for non-notebook, eg spyder environ
#https://jakevdp.github.io/PythonDataScienceHandbook/04.00-introduction-to-matplotlib.html recomends *inline*!
#show current one:
#%matplotlib
#%matplotlib --list
#interactive plots:
#%matplotlib notebook
#static images of your plot:
%matplotlib inline
#may play with this one and other magics (btw default is probably agg)
#%matplotlib nbagg

###themes/styles: https://matplotlib.org/stable/gallery/style_sheets/style_sheets_reference.html
#https://jakevdp.github.io/PythonDataScienceHandbook/04.11-settings-and-stylesheets.html
#https://matplotlib.org/stable/tutorials/introductory/customizing.html
#here more about art and style than under the hood functionality as with magics, explore and experiment
#many may find 'default' or seaborn ones more pleasing; my fav 'classic' is back from 90s ;)
#plt.style.available #list available styles :) may install more
#plt.style.use('default') # more delicate subtle than classic
plt.style.use('classic')  #  'seaborn-whitegrid' 'seaborn-white' 'seaborn-poster'
# btw: magics v theme/style sequence matters, eg if i specify classic style before inline magic, i wouldnt get grey bounding box im getting

# 1. Dataset 1 Import

In [10]:
df1=pd.read_csv("https://github.com/XiaoLiang28/Datamanagement/raw/main/enrollment_2021.csv")

In [11]:
df1

Unnamed: 0   Unnamed: 1     Unnamed: 2  \
0     2020-2021 Enrollment Data - District Counts          NaN            NaN   
1                                     County Code  County Name  District Code   
2                                              01     Atlantic           0010   
3                                              01     Atlantic           0110   
4                                              01     Atlantic           0120   
..                                            ...          ...            ...   
668                                            80     Charters           8050   
669                                            80     Charters           8060   
670                                            80     Charters           8065   
671                                            80     Charters           8140   
672                              End of worksheet          NaN            NaN   

                                     Unnamed: 3        Unnamed: 4 Unnamed: 5  \
0                                           NaN               NaN        NaN   
1                                 District Name  Total Enrollment      White   
2               Absecon Public Schools District               887        447   
3                 Atlantic City School District              6450        265   
4    Atlantic County Vocational School District              1713        516   
..                                          ...               ...        ...   
668                        Unity Charter School               245        123   
669      University Academy Charter High School               439         18   
670           University Heights Charter School               858          0   
671                  The Village Charter School               363          4   
672                                         NaN               NaN        NaN   

    Unnamed: 6 Unnamed: 7 Unnamed: 8 Unnamed: 9  ...  Unnamed: 32  \
0          NaN        NaN        NaN        NaN  ...          NaN   
1       %White      Black     %Black   Hispanic  ...  Tenth Grade   
2         50.4        133         15        208  ...            0   
3          4.1       2147       33.3       2847  ...          462   
4         30.1        296       17.3        721  ...          399   
..         ...        ...        ...        ...  ...          ...   
668       50.2         40       16.3         28  ...            0   
669        4.1        240       54.7        142  ...          118   
670          0        724       84.4        133  ...            0   
671        1.1        345         95         14  ...            0   
672        NaN        NaN        NaN        NaN  ...          NaN   

        Unnamed: 33    Unnamed: 34 Unnamed: 35  Unnamed: 36     Unnamed: 37  \
0               NaN            NaN         NaN          NaN             NaN   
1    Eleventh Grade  Twelfth Grade    Ungraded  %Free Lunch  %Reduced Lunch   
2                 0              0          25         40.8             5.9   
3               405            369         286         81.5             3.6   
4               355            362         160         48.6             9.6   
..              ...            ...         ...          ...             ...   
668               0              0           0          9.8             1.6   
669             105            100           0         53.3             9.8   
670               0              0           0         73.1            13.9   
671               0              0           0         64.5             5.5   
672             NaN            NaN         NaN          NaN             NaN   

           Unnamed: 38 Unnamed: 39 Unnamed: 40 Unnamed: 41  
0                  NaN         NaN         NaN         NaN  
1    %English Learners    %Migrant   %Military   %Homeless  
2                  8.7           0         0.8         0.2  
3                 16.1           0           0         2.2  
4                    0

In [12]:
df1.drop([0,672],inplace=True)

In [13]:
df1

Unnamed: 0   Unnamed: 1     Unnamed: 2  \
1    County Code  County Name  District Code   
2             01     Atlantic           0010   
3             01     Atlantic           0110   
4             01     Atlantic           0120   
5             01     Atlantic           0125   
..           ...          ...            ...   
667           80     Charters           8010   
668           80     Charters           8050   
669           80     Charters           8060   
670           80     Charters           8065   
671           80     Charters           8140   

                                            Unnamed: 3        Unnamed: 4  \
1                                        District Name  Total Enrollment   
2                      Absecon Public Schools District               887   
3                        Atlantic City School District              6450   
4           Atlantic County Vocational School District              1713   
5     Atlantic County Special Services School District               306   
..                                                 ...               ...   
667  Union County Teams Charter School-High School/...               400   
668                               Unity Charter School               245   
669             University Academy Charter High School               439   
670                  University Heights Charter School               858   
671                         The Village Charter School               363   

    Unnamed: 5 Unnamed: 6 Unnamed: 7 Unnamed: 8 Unnamed: 9  ...  Unnamed: 32  \
1        White     %White      Black     %Black   Hispanic  ...  Tenth Grade   
2          447       50.4        133         15        208  ...            0   
3          265        4.1       2147       33.3       2847  ...          462   
4          516       30.1        296       17.3        721  ...          399   
5           95         31         82       26.8        108  ...            3   
..         ...        ...        ...        ...        ...  ...          ...   
667          1        0.3        242       60.5        153  ...           33   
668        123       50.2         40       16.3         28  ...            0   
669         18        4.1        240       54.7        142  ...          118   
670          0          0        724       84.4        133  ...            0   
671          4        1.1        345         95         14  ...            0   

        Unnamed: 33    Unnamed: 34 Unnamed: 35  Unnamed: 36     Unnamed: 37  \
1    Eleventh Grade  Twelfth Grade    Ungraded  %Free Lunch  %Reduced Lunch   
2                 0              0          25         40.8             5.9   
3               405            369         286         81.5             3.6   
4               355            362         160         48.6             9.6   
5                 5             13         244         39.5             5.9   
..              ...            ...         ...          ...             ...   
667              34             39           0         61.3              10   
668               0              0           0          9.8             1.6   
669             105            100           0         53.3             9.8   
670               0              0           0         73.1            13.9   
671               0              0           0         64.5             5.5   

           Unnamed: 38 Unnamed: 39 Unnamed: 40 Unnamed: 41  
1    %English Learners    %Migrant   %Military   %Homeless  
2                  8.7           0         0.8         0.2  
3                 16.1           0           0         2.2  
4                    0           0         2.5         0.6  
5                  0.3           0         0.3           1  
..                 ...         ...         ...         ...  
667                  4           0           0         4.8  
668                1.2           0           0           0  
669                  0           0           0           

In [14]:
df1 = df1.rename(columns={'Unnamed: 0': 'County Code', 'Unnamed: 1': 'County Name', 'Unnamed: 2': 'District Code', 'Unnamed: 3': 'District Name', 'Unnamed: 4': 'Total Enrollment', 'Unnamed: 5': 'White', 'Unnamed: 6': '%White', 'Unnamed: 7': 'Black', 'Unnamed: 8': '%Black', 'Unnamed: 9': 'Hispanic', 'Unnamed: 10': '%Hispanic', 'Unnamed: 11': 'Asian', 'Unnamed: 12': '%Asian', 'Unnamed: 13': 'Native American', 'Unnamed: 14': '%Native American', 'Unnamed: 15': 'Hawaiian Native', 'Unnamed: 16': '%Hawaiian Native', 'Unnamed: 17': 'Two or More Races', 'Unnamed 18': '%Two or More Races'})

In [15]:
df1

County Code  County Name  District Code  \
1    County Code  County Name  District Code   
2             01     Atlantic           0010   
3             01     Atlantic           0110   
4             01     Atlantic           0120   
5             01     Atlantic           0125   
..           ...          ...            ...   
667           80     Charters           8010   
668           80     Charters           8050   
669           80     Charters           8060   
670           80     Charters           8065   
671           80     Charters           8140   

                                         District Name  Total Enrollment  \
1                                        District Name  Total Enrollment   
2                      Absecon Public Schools District               887   
3                        Atlantic City School District              6450   
4           Atlantic County Vocational School District              1713   
5     Atlantic County Special Services School District               306   
..                                                 ...               ...   
667  Union County Teams Charter School-High School/...               400   
668                               Unity Charter School               245   
669             University Academy Charter High School               439   
670                  University Heights Charter School               858   
671                         The Village Charter School               363   

     White  %White  Black  %Black  Hispanic  ...  Unnamed: 32     Unnamed: 33  \
1    White  %White  Black  %Black  Hispanic  ...  Tenth Grade  Eleventh Grade   
2      447    50.4    133      15       208  ...            0               0   
3      265     4.1   2147    33.3      2847  ...          462             405   
4      516    30.1    296    17.3       721  ...          399             355   
5       95      31     82    26.8       108  ...            3               5   
..     ...     ...    ...     ...       ...  ...          ...             ...   
667      1     0.3    242    60.5       153  ...           33              34   
668    123    50.2     40    16.3        28  ...            0               0   
669     18     4.1    240    54.7       142  ...          118             105   
670      0       0    724    84.4       133  ...            0               0   
671      4     1.1    345      95        14  ...            0               0   

       Unnamed: 34 Unnamed: 35  Unnamed: 36     Unnamed: 37  \
1    Twelfth Grade    Ungraded  %Free Lunch  %Reduced Lunch   
2                0          25         40.8             5.9   
3              369         286         81.5             3.6   
4              362         160         48.6             9.6   
5               13         244         39.5             5.9   
..             ...         ...          ...             ...   
667             39           0         61.3              10   
668              0           0          9.8             1.6   
669            100           0         53.3             9.8   
670              0           0         73.1            13.9   
671              0           0         64.5             5.5   

           Unnamed: 38 Unnamed: 39 Unnamed: 40 Unnamed: 41  
1    %English Learners    %Migrant   %Military   %Homeless  
2                  8.7           0         0.8         0.2  
3                 16.1           0           0         2.2  
4                    0           0         2.5         0.6  
5                  0.3           0         0.3           1  
..                 ...         ...         ...         ...  
667                  4           0           0         4.8  
668                1.2           0           0           0  
669                  0           0           0           0  
670                6.4           0           0           0  
671                  0           0           0           0  

[671 rows x 42 columns]

In [16]:
df1=df1.rename(columns={'Unnamed: 18': '%Two or More Races'})

In [17]:
df1.drop(1,inplace=True)

In [18]:
df1

County Code County Name District Code  \
2            01    Atlantic          0010   
3            01    Atlantic          0110   
4            01    Atlantic          0120   
5            01    Atlantic          0125   
6            01    Atlantic          0570   
..          ...         ...           ...   
667          80    Charters          8010   
668          80    Charters          8050   
669          80    Charters          8060   
670          80    Charters          8065   
671          80    Charters          8140   

                                         District Name Total Enrollment White  \
2                      Absecon Public Schools District              887   447   
3                        Atlantic City School District             6450   265   
4           Atlantic County Vocational School District             1713   516   
5     Atlantic County Special Services School District              306    95   
6                    Brigantine Public School District              444   314   
..                                                 ...              ...   ...   
667  Union County Teams Charter School-High School/...              400     1   
668                               Unity Charter School              245   123   
669             University Academy Charter High School              439    18   
670                  University Heights Charter School              858     0   
671                         The Village Charter School              363     4   

    %White Black %Black Hispanic  ... Unnamed: 32 Unnamed: 33 Unnamed: 34  \
2     50.4   133     15      208  ...           0           0           0   
3      4.1  2147   33.3     2847  ...         462         405         369   
4     30.1   296   17.3      721  ...         399         355         362   
5       31    82   26.8      108  ...           3           5          13   
6     70.7    18    4.1       62  ...           0           0           0   
..     ...   ...    ...      ...  ...         ...         ...         ...   
667    0.3   242   60.5      153  ...          33          34          39   
668   50.2    40   16.3       28  ...           0           0           0   
669    4.1   240   54.7      142  ...         118         105         100   
670      0   724   84.4      133  ...           0           0           0   
671    1.1   345     95       14  ...           0           0           0   

    Unnamed: 35 Unnamed: 36 Unnamed: 37 Unnamed: 38 Unnamed: 39 Unnamed: 40  \
2            25        40.8         5.9         8.7           0         0.8   
3           286        81.5         3.6        16.1           0           0   
4           160        48.6         9.6           0           0         2.5   
5           244        39.5         5.9         0.3           0         0.3   
6            12        33.8         8.3         3.4           0         2.3   
..          ...         ...         ...         ...         ...         ...   
667           0        61.3          10           4           0           0   
668           0         9.8         1.6         1.2           0           0   
669           0        53.3         9.8           0           0           0   
670           0        73.1        13.9         6.4           0           0   
671           0        64.5         5.5           0           0           0   

    Unnamed: 41  
2           0.2  
3           2.2  
4           0.6  
5             1  
6           0.5  
..          ...  
667         4.8  
668           0  
669           0  
670           0  
671           0  

[670 rows x 42 columns]

In [19]:
pd.set_option('display.max_columns', None)

In [20]:
df1

County Code County Name District Code  \
2            01    Atlantic          0010   
3            01    Atlantic          0110   
4            01    Atlantic          0120   
5            01    Atlantic          0125   
6            01    Atlantic          0570   
..          ...         ...           ...   
667          80    Charters          8010   
668          80    Charters          8050   
669          80    Charters          8060   
670          80    Charters          8065   
671          80    Charters          8140   

                                         District Name Total Enrollment White  \
2                      Absecon Public Schools District              887   447   
3                        Atlantic City School District             6450   265   
4           Atlantic County Vocational School District             1713   516   
5     Atlantic County Special Services School District              306    95   
6                    Brigantine Public School District              444   314   
..                                                 ...              ...   ...   
667  Union County Teams Charter School-High School/...              400     1   
668                               Unity Charter School              245   123   
669             University Academy Charter High School              439    18   
670                  University Heights Charter School              858     0   
671                         The Village Charter School              363     4   

    %White Black %Black Hispanic %Hispanic Asian %Asian Native American  \
2     50.4   133     15      208      23.4    57    6.4               0   
3      4.1  2147   33.3     2847      44.1  1046   16.2               1   
4     30.1   296   17.3      721      42.1   102      6               5   
5       31    82   26.8      108      35.3    11    3.6               1   
6     70.7    18    4.1       62        14    48   10.8               0   
..     ...   ...    ...      ...       ...   ...    ...             ...   
667    0.3   242   60.5      153      38.3     4      1               0   
668   50.2    40   16.3       28      11.4    37   15.1               0   
669    4.1   240   54.7      142      32.3    39    8.9               0   
670      0   724   84.4      133      15.5     1    0.1               0   
671    1.1   345     95       14       3.9     0      0               0   

    %Native American Hawaiian Native %Hawaiian Native Two or More Races  \
2                  0               0                0                42   
3                  0              42              0.7               102   
4                0.3               9              0.5                64   
5                0.3               5              1.6                 4   
6                  0               0                0                 2   
..               ...             ...              ...               ...   
667                0               0                0                 0   
668                0               0                0                17   
669                0               0                0                 0   
670                0               0                0                 0   
671                0               0                0                 0   

    %Two or More Races Unnamed: 19 Unnamed: 20 Unnamed: 21 Unnamed: 22  \
2                  4.7           0          48           0          83   
3                  1.6           0         340           0         379   
4                  3.7           0           0           0           0   
5                  1.3           0           4           0           0   
6                  0.5           0          56           0          34   
..                 ...         ...         ...         ...         ...   
667                  0           0           0           0          16   
668                6.9           0           0           0          28   
669                  0

In [21]:
df1.drop(['Unnamed: 19', 'Unnamed: 20', 'Unnamed: 21', 'Unnamed: 22', 'Unnamed: 23', 'Unnamed: 24', 'Unnamed: 25', 'Unnamed: 26', 'Unnamed: 27', 'Unnamed: 28', 'Unnamed: 29', 'Unnamed: 30', 'Unnamed: 31', 'Unnamed: 32', 'Unnamed: 33', 'Unnamed: 34', 'Unnamed: 35', 'Unnamed: 36', 'Unnamed: 37', 'Unnamed: 38', 'Unnamed: 39', 'Unnamed: 40', 'Unnamed: 41'],axis=1, inplace=True)

In [22]:
df1

County Code County Name District Code  \
2            01    Atlantic          0010   
3            01    Atlantic          0110   
4            01    Atlantic          0120   
5            01    Atlantic          0125   
6            01    Atlantic          0570   
..          ...         ...           ...   
667          80    Charters          8010   
668          80    Charters          8050   
669          80    Charters          8060   
670          80    Charters          8065   
671          80    Charters          8140   

                                         District Name Total Enrollment White  \
2                      Absecon Public Schools District              887   447   
3                        Atlantic City School District             6450   265   
4           Atlantic County Vocational School District             1713   516   
5     Atlantic County Special Services School District              306    95   
6                    Brigantine Public School District              444   314   
..                                                 ...              ...   ...   
667  Union County Teams Charter School-High School/...              400     1   
668                               Unity Charter School              245   123   
669             University Academy Charter High School              439    18   
670                  University Heights Charter School              858     0   
671                         The Village Charter School              363     4   

    %White Black %Black Hispanic %Hispanic Asian %Asian Native American  \
2     50.4   133     15      208      23.4    57    6.4               0   
3      4.1  2147   33.3     2847      44.1  1046   16.2               1   
4     30.1   296   17.3      721      42.1   102      6               5   
5       31    82   26.8      108      35.3    11    3.6               1   
6     70.7    18    4.1       62        14    48   10.8               0   
..     ...   ...    ...      ...       ...   ...    ...             ...   
667    0.3   242   60.5      153      38.3     4      1               0   
668   50.2    40   16.3       28      11.4    37   15.1               0   
669    4.1   240   54.7      142      32.3    39    8.9               0   
670      0   724   84.4      133      15.5     1    0.1               0   
671    1.1   345     95       14       3.9     0      0               0   

    %Native American Hawaiian Native %Hawaiian Native Two or More Races  \
2                  0               0                0                42   
3                  0              42              0.7               102   
4                0.3               9              0.5                64   
5                0.3               5              1.6                 4   
6                  0               0                0                 2   
..               ...             ...              ...               ...   
667                0               0                0                 0   
668                0               0                0                17   
669                0               0                0                 0   
670                0               0                0                 0   
671                0               0                0                 0   

    %Two or More Races  
2                  4.7  
3                  1.6  
4                  3.7  
5                  1.3  
6                  0.5  
..                 ...  
667                  0  
668                6.9  
669                  0  
670                  0  
671                  0  

[670 rows x 19 columns]

In [23]:
select_county = df1.loc[df1['County Name'] == 'Camden'] # I only want data of Camden County
print (select_county)

    County Code County Name District Code  \
141          07      Camden          0150   
142          07      Camden          0190   
143          07      Camden          0260   
144          07      Camden          0330   
145          07      Camden          0340   
146          07      Camden          0390   
147          07      Camden          0580   
148          07      Camden          0680   
149          07      Camden          0700   
150          07      Camden          0800   
151          07      Camden          0880   
152          07      Camden          0940   
153          07      Camden          1255   
154          07      Camden          1720   
155          07      Camden          1770   
156          07      Camden          1780   
157          07      Camden          1799   
158          07      Camden          1801   
159          07      Camden          1802   
160          07      Camden          1880   
161          07      Camden          1890   
162       

In [24]:
df1=select_county

In [25]:
df1

County Code County Name District Code  \
141          07      Camden          0150   
142          07      Camden          0190   
143          07      Camden          0260   
144          07      Camden          0330   
145          07      Camden          0340   
146          07      Camden          0390   
147          07      Camden          0580   
148          07      Camden          0680   
149          07      Camden          0700   
150          07      Camden          0800   
151          07      Camden          0880   
152          07      Camden          0940   
153          07      Camden          1255   
154          07      Camden          1720   
155          07      Camden          1770   
156          07      Camden          1780   
157          07      Camden          1799   
158          07      Camden          1801   
159          07      Camden          1802   
160          07      Camden          1880   
161          07      Camden          1890   
162          07      Camden          1900   
163          07      Camden          2540   
164          07      Camden          2560   
165          07      Camden          2670   
166          07      Camden          2890   
167          07      Camden          3110   
168          07      Camden          3420   
169          07      Camden          3770   
170          07      Camden          4060   
171          07      Camden          4110   
172          07      Camden          4590   
173          07      Camden          4790   
174          07      Camden          5035   
175          07      Camden          5080   
176          07      Camden          5400   
177          07      Camden          5560   
178          07      Camden          5820   
179          07      Camden          5900   

                                         District Name Total Enrollment White  \
141                     Audubon Public School District             1444  1235   
142                         Barrington School District              563   432   
143                    Bellmawr Public School District             1166   671   
144                     Berlin Borough School District              807   659   
145                    Berlin Township School District              604   356   
146          Black Horse Pike Regional School District             3478  1840   
147                   Brooklawn Public School District              285   157   
148                        Camden City School District             7343    68   
149            Camden County Technical School District             2245   664   
150                        Cherry Hill School District            10469  5774   
151               Clementon Elementary School District              516   174   
152                Collingswood Public School District             2200  1323   
153     Eastern Camden County Regional School District             1926  1144   
154               Gibbsboro Elementary School District              276   177   
155             Gloucester City Public School District             2220  1372   
156                 Gloucester Township Public Schools             6368  3076   
157  Kipp: Cooper Norcross A New Jersey Nonprofit C...             1775     5   
158                                   Camden Prep Inc.              949     1   
159                     Mastery Schools Of Camden Inc.             2737    10   
160                     Haddon Heights School District             1514  1131   
161                    Haddon Township School District             1971  1576   
162                        Haddonfield School District             2645  2315   
163                     Laurel Springs School District              167   107   
164                            Lawnside School Distric              308     4   
165                  Lindenwold Public School District             2926   219   
166                           Magnolia School District              375   188   
167             

# 2. Dataset 2 Import

In [26]:
df2=pd.read_csv("https://github.com/XiaoLiang28/Datamanagement/raw/main/Teacher's%20Race%202021.csv")

In [27]:
df2

Co Code    County  Dist Code                         District  \
0               01  Atlantic       10.0  Absecon Public Schools District   
1               01  Atlantic       10.0  Absecon Public Schools District   
2               01  Atlantic       10.0  Absecon Public Schools District   
3               01  Atlantic       10.0  Absecon Public Schools District   
4               01  Atlantic      110.0    Atlantic City School District   
...            ...       ...        ...                              ...   
2684            80  Charters     8140.0       The Village Charter School   
2685            80  Charters     8140.0       The Village Charter School   
2686            80  Charters     8140.0       The Village Charter School   
2687            80  Charters     8140.0       The Village Charter School   
2688  end of table       NaN        NaN                              NaN   

                      Position White  %White  Black  %Black  Hispanic  \
0               Administrators   5.5   100.0    0.0     0.0       0.0   
1              Special Service   9.7    94.2    0.0     0.0       0.6   
2                      Teacher  77.8    97.5    0.0     0.0       1.0   
3     Supervisors/Coordinators   0.5   100.0    0.0     0.0       0.0   
4               Administrators   6.5    19.7   23.0    69.7       1.5   
...                        ...   ...     ...    ...     ...       ...   
2684            Administrators   2.0    66.7    1.0    33.3       0.0   
2685           Special Service   0.0     0.0    3.0   100.0       0.0   
2686                   Teacher  22.0    73.3    6.0    20.0       1.0   
2687  Supervisors/Coordinators   0.0     0.0    1.0   100.0       0.0   
2688                       NaN   NaN     NaN    NaN     NaN       NaN   

      %Hispanic  Asian  %Asian  American Indian  %American Indian  \
0           0.0    0.0     0.0              0.0               0.0   
1           5.8    0.0     0.0              0.0               0.0   
2           1.3    0.0     0.0              0.0               0.0   
3           0.0    0.0     0.0              0.0               0.0   
4           4.5    0.0     0.0              0.0               0.0   
...         ...    ...     ...              ...               ...   
2684        0.0    0.0     0.0              0.0               0.0   
2685        0.0    0.0     0.0              0.0               0.0   
2686        3.3    1.0     3.3              0.0               0.0   
2687        0.0    0.0     0.0              0.0               0.0   
2688        NaN    NaN     NaN              NaN               NaN   

      Hawaiian Native  %Hawaiian Native  Two or More Races  \
0                 0.0               0.0                0.0   
1                 0.0               0.0                0.0   
2                 0.0               0.0                1.0   
3                 0.0               0.0                0.0   
4                 0.0               0.0                2.0   
...               ...               ...                ...   
2684              0.0               0.0                0.0   
2685              0.0               0.0                0.0   
2686              0.0               0.0                0.0   
2687              0.0               0.0                0.0   
2688              NaN               NaN                NaN   

      %Two or More Races Total  Male  %Male Female  %Female %Non Binary  
0                    0.0   5.5   3.0   54.5    2.5     45.5         <.1  
1                    0.0  10.3   0.0    0.0   10.3    100.0         <.1  
2                    1.3  79.8  15.0   18.8   64.8     81.2         <.1  
3                    0.0   0.5   0.0    0.0    0.5    100.0         <.1  
4                    6.1  33.0  10.5   31.8   22.5     68.2         <.1  
...                  ...   ...   ...    ...    ...      ...         ...  
2684                 0.0   3.0   1.0   33.3    2.0     66.7         <.1  
2685                 0.0   3.0   0.0    0.0    3.0    1

In [28]:
pd.set_option('display.max_columns', None)

In [29]:
df2

Co Code    County  Dist Code                         District  \
0               01  Atlantic       10.0  Absecon Public Schools District   
1               01  Atlantic       10.0  Absecon Public Schools District   
2               01  Atlantic       10.0  Absecon Public Schools District   
3               01  Atlantic       10.0  Absecon Public Schools District   
4               01  Atlantic      110.0    Atlantic City School District   
...            ...       ...        ...                              ...   
2684            80  Charters     8140.0       The Village Charter School   
2685            80  Charters     8140.0       The Village Charter School   
2686            80  Charters     8140.0       The Village Charter School   
2687            80  Charters     8140.0       The Village Charter School   
2688  end of table       NaN        NaN                              NaN   

                      Position White  %White  Black  %Black  Hispanic  \
0               Administrators   5.5   100.0    0.0     0.0       0.0   
1              Special Service   9.7    94.2    0.0     0.0       0.6   
2                      Teacher  77.8    97.5    0.0     0.0       1.0   
3     Supervisors/Coordinators   0.5   100.0    0.0     0.0       0.0   
4               Administrators   6.5    19.7   23.0    69.7       1.5   
...                        ...   ...     ...    ...     ...       ...   
2684            Administrators   2.0    66.7    1.0    33.3       0.0   
2685           Special Service   0.0     0.0    3.0   100.0       0.0   
2686                   Teacher  22.0    73.3    6.0    20.0       1.0   
2687  Supervisors/Coordinators   0.0     0.0    1.0   100.0       0.0   
2688                       NaN   NaN     NaN    NaN     NaN       NaN   

      %Hispanic  Asian  %Asian  American Indian  %American Indian  \
0           0.0    0.0     0.0              0.0               0.0   
1           5.8    0.0     0.0              0.0               0.0   
2           1.3    0.0     0.0              0.0               0.0   
3           0.0    0.0     0.0              0.0               0.0   
4           4.5    0.0     0.0              0.0               0.0   
...         ...    ...     ...              ...               ...   
2684        0.0    0.0     0.0              0.0               0.0   
2685        0.0    0.0     0.0              0.0               0.0   
2686        3.3    1.0     3.3              0.0               0.0   
2687        0.0    0.0     0.0              0.0               0.0   
2688        NaN    NaN     NaN              NaN               NaN   

      Hawaiian Native  %Hawaiian Native  Two or More Races  \
0                 0.0               0.0                0.0   
1                 0.0               0.0                0.0   
2                 0.0               0.0                1.0   
3                 0.0               0.0                0.0   
4                 0.0               0.0                2.0   
...               ...               ...                ...   
2684              0.0               0.0                0.0   
2685              0.0               0.0                0.0   
2686              0.0               0.0                0.0   
2687              0.0               0.0                0.0   
2688              NaN               NaN                NaN   

      %Two or More Races Total  Male  %Male Female  %Female %Non Binary  
0                    0.0   5.5   3.0   54.5    2.5     45.5         <.1  
1                    0.0  10.3   0.0    0.0   10.3    100.0         <.1  
2                    1.3  79.8  15.0   18.8   64.8     81.2         <.1  
3                    0.0   0.5   0.0    0.0    0.5    100.0         <.1  
4                    6.1  33.0  10.5   31.8   22.5     68.2         <.1  
...                  ...   ...   ...    ...    ...      ...         ...  
2684                 0.0   3.0   1.0   33.3    2.0     66.7         <.1  
2685                 0.0   3.0   0.0    0.0    3.0    1

In [30]:
df2.drop(df2.tail(1).index,inplace=True)

In [31]:
df2

Co Code    County  Dist Code                           District  \
0         01  Atlantic       10.0    Absecon Public Schools District   
1         01  Atlantic       10.0    Absecon Public Schools District   
2         01  Atlantic       10.0    Absecon Public Schools District   
3         01  Atlantic       10.0    Absecon Public Schools District   
4         01  Atlantic      110.0      Atlantic City School District   
...      ...       ...        ...                                ...   
2683      80  Charters     8065.0  University Heights Charter School   
2684      80  Charters     8140.0         The Village Charter School   
2685      80  Charters     8140.0         The Village Charter School   
2686      80  Charters     8140.0         The Village Charter School   
2687      80  Charters     8140.0         The Village Charter School   

                      Position White  %White  Black  %Black  Hispanic  \
0               Administrators   5.5   100.0    0.0     0.0       0.0   
1              Special Service   9.7    94.2    0.0     0.0       0.6   
2                      Teacher  77.8    97.5    0.0     0.0       1.0   
3     Supervisors/Coordinators   0.5   100.0    0.0     0.0       0.0   
4               Administrators   6.5    19.7   23.0    69.7       1.5   
...                        ...   ...     ...    ...     ...       ...   
2683  Supervisors/Coordinators   0.0     0.0    1.0   100.0       0.0   
2684            Administrators   2.0    66.7    1.0    33.3       0.0   
2685           Special Service   0.0     0.0    3.0   100.0       0.0   
2686                   Teacher  22.0    73.3    6.0    20.0       1.0   
2687  Supervisors/Coordinators   0.0     0.0    1.0   100.0       0.0   

      %Hispanic  Asian  %Asian  American Indian  %American Indian  \
0           0.0    0.0     0.0              0.0               0.0   
1           5.8    0.0     0.0              0.0               0.0   
2           1.3    0.0     0.0              0.0               0.0   
3           0.0    0.0     0.0              0.0               0.0   
4           4.5    0.0     0.0              0.0               0.0   
...         ...    ...     ...              ...               ...   
2683        0.0    0.0     0.0              0.0               0.0   
2684        0.0    0.0     0.0              0.0               0.0   
2685        0.0    0.0     0.0              0.0               0.0   
2686        3.3    1.0     3.3              0.0               0.0   
2687        0.0    0.0     0.0              0.0               0.0   

      Hawaiian Native  %Hawaiian Native  Two or More Races  \
0                 0.0               0.0                0.0   
1                 0.0               0.0                0.0   
2                 0.0               0.0                1.0   
3                 0.0               0.0                0.0   
4                 0.0               0.0                2.0   
...               ...               ...                ...   
2683              0.0               0.0                0.0   
2684              0.0               0.0                0.0   
2685              0.0               0.0                0.0   
2686              0.0               0.0                0.0   
2687              0.0               0.0                0.0   

      %Two or More Races Total  Male  %Male Female  %Female %Non Binary  
0                    0.0   5.5   3.0   54.5    2.5     45.5         <.1  
1                    0.0  10.3   0.0    0.0   10.3    100.0         <.1  
2                    1.3  79.8  15.0   18.8   64.8     81.2         <.1  
3                    0.0   0.5   0.0    0.0    0.5    100.0         <.1  
4                    6.1  33.0  10.5   31.8   22.5     68.2         <.1  
...                  ...   ...   ...    ...    ...      ...         ...  
2683                 0.0   1.0   0.0    0.0    1.0    100.0         <.1  
2684                 0.0   3.0   1.0   33.3    2.0     66.7         <.1  
2685                 0.

In [32]:
df2 = df2.rename(columns={'Co Code': 'County Code'})

In [33]:
df2 = df2.rename(columns={'County': 'County Name', 'Dist Code': 'District Code', 'District': 'District Name'})

In [34]:
df2.drop(['Total', 'Male', '%Male', 'Female', '%Female', '%Non Binary'],axis=1, inplace=True)

In [35]:
df2 = df2.rename(columns={'American Indian': 'Native American', '%American Indian': '%Native American'})

In [36]:
df2

County Code County Name  District Code  \
0             01    Atlantic           10.0   
1             01    Atlantic           10.0   
2             01    Atlantic           10.0   
3             01    Atlantic           10.0   
4             01    Atlantic          110.0   
...          ...         ...            ...   
2683          80    Charters         8065.0   
2684          80    Charters         8140.0   
2685          80    Charters         8140.0   
2686          80    Charters         8140.0   
2687          80    Charters         8140.0   

                          District Name                  Position White  \
0       Absecon Public Schools District            Administrators   5.5   
1       Absecon Public Schools District           Special Service   9.7   
2       Absecon Public Schools District                   Teacher  77.8   
3       Absecon Public Schools District  Supervisors/Coordinators   0.5   
4         Atlantic City School District            Administrators   6.5   
...                                 ...                       ...   ...   
2683  University Heights Charter School  Supervisors/Coordinators   0.0   
2684         The Village Charter School            Administrators   2.0   
2685         The Village Charter School           Special Service   0.0   
2686         The Village Charter School                   Teacher  22.0   
2687         The Village Charter School  Supervisors/Coordinators   0.0   

      %White  Black  %Black  Hispanic  %Hispanic  Asian  %Asian  \
0      100.0    0.0     0.0       0.0        0.0    0.0     0.0   
1       94.2    0.0     0.0       0.6        5.8    0.0     0.0   
2       97.5    0.0     0.0       1.0        1.3    0.0     0.0   
3      100.0    0.0     0.0       0.0        0.0    0.0     0.0   
4       19.7   23.0    69.7       1.5        4.5    0.0     0.0   
...      ...    ...     ...       ...        ...    ...     ...   
2683     0.0    1.0   100.0       0.0        0.0    0.0     0.0   
2684    66.7    1.0    33.3       0.0        0.0    0.0     0.0   
2685     0.0    3.0   100.0       0.0        0.0    0.0     0.0   
2686    73.3    6.0    20.0       1.0        3.3    1.0     3.3   
2687     0.0    1.0   100.0       0.0        0.0    0.0     0.0   

      Native American  %Native American  Hawaiian Native  %Hawaiian Native  \
0                 0.0               0.0              0.0               0.0   
1                 0.0               0.0              0.0               0.0   
2                 0.0               0.0              0.0               0.0   
3                 0.0               0.0              0.0               0.0   
4                 0.0               0.0              0.0               0.0   
...               ...               ...              ...               ...   
2683              0.0               0.0              0.0               0.0   
2684              0.0               0.0              0.0               0.0   
2685              0.0               0.0              0.0               0.0   
2686              0.0               0.0              0.0               0.0   
2687              0.0               0.0              0.0               0.0   

      Two or More Races  %Two or More Races  
0                   0.0                 0.0  
1                   0.0                 0.0  
2                   1.0                 1.3  
3                   0.0                 0.0  
4                   2.0                 6.1  
...                 ...                 ...  
2683                0.0                 0.0  
2684                0.0                 0.0  
2685                0.0                 0.0  
2686                0.0                 0.0  
2687                0.0                 0.0  

[2688 rows x 19 columns]

In [37]:
selectcounty = df2.loc[df2['County Name'] == 'Camden'] # Only select data of Camden County
print (selectcounty)

    County Code County Name  District Code                     District Name  \
556          07      Camden          150.0    Audubon Public School District   
557          07      Camden          150.0    Audubon Public School District   
558          07      Camden          150.0    Audubon Public School District   
559          07      Camden          150.0    Audubon Public School District   
560          07      Camden          190.0        Barrington School District   
..          ...         ...            ...                               ...   
711          07      Camden         5820.0  Winslow Township School District   
712          07      Camden         5900.0         Woodlynne School District   
713          07      Camden         5900.0         Woodlynne School District   
714          07      Camden         5900.0         Woodlynne School District   
715          07      Camden         5900.0         Woodlynne School District   

                     Position  White  %

In [38]:
df2=selectcounty
df2

County Code County Name  District Code                     District Name  \
556          07      Camden          150.0    Audubon Public School District   
557          07      Camden          150.0    Audubon Public School District   
558          07      Camden          150.0    Audubon Public School District   
559          07      Camden          150.0    Audubon Public School District   
560          07      Camden          190.0        Barrington School District   
..          ...         ...            ...                               ...   
711          07      Camden         5820.0  Winslow Township School District   
712          07      Camden         5900.0         Woodlynne School District   
713          07      Camden         5900.0         Woodlynne School District   
714          07      Camden         5900.0         Woodlynne School District   
715          07      Camden         5900.0         Woodlynne School District   

                     Position  White  %White  Black  %Black  Hispanic  \
556            Administrators    8.1   100.0    0.0     0.0       0.0   
557           Special Service   20.3    96.2    0.0     0.0       0.0   
558                   Teacher  119.2    97.5    0.0     0.0       1.0   
559  Supervisors/Coordinators    1.8   100.0    0.0     0.0       0.0   
560            Administrators    4.9   100.0    0.0     0.0       0.0   
..                        ...    ...     ...    ...     ...       ...   
711  Supervisors/Coordinators    2.0    66.7    1.0    33.3       0.0   
712            Administrators    1.0    33.3    2.0    66.7       0.0   
713           Special Service    3.0   100.0    0.0     0.0       0.0   
714                   Teacher   31.1    94.0    2.0     6.0       0.0   
715  Supervisors/Coordinators    1.0   100.0    0.0     0.0       0.0   

     %Hispanic  Asian  %Asian  Native American  %Native American  \
556        0.0    0.0     0.0              0.0               0.0   
557        0.0    0.8     3.8              0.0               0.0   
558        0.8    2.0     1.6              0.0               0.0   
559        0.0    0.0     0.0              0.0               0.0   
560        0.0    0.0     0.0              0.0               0.0   
..         ...    ...     ...              ...               ...   
711        0.0    0.0     0.0              0.0               0.0   
712        0.0    0.0     0.0              0.0               0.0   
713        0.0    0.0     0.0              0.0               0.0   
714        0.0    0.0     0.0              0.0               0.0   
715        0.0    0.0     0.0              0.0               0.0   

     Hawaiian Native  %Hawaiian Native  Two or More Races  %Two or More Races  
556              0.0               0.0                0.0                 0.0  
557              0.0               0.0                0.0                 0.0  
558              0.0               0.0                0.0                 0.0  
559              0.0               0.0                0.0                 0.0  
560              0.0               0.0                0.0                 0.0  
..               ...               ...                ...                 ...  
711              0.0               0.0                0.0                 0.0  
712              0.0               0.0                0.0                 0.0  
713              0.0               0.0                0.0                 0.0  
714              0.0               0.0                0.0                 0.0  
715              0.0               0.0                0.0                 0.0  

[160 rows x 19 columns]

In [39]:
df2.dtypes

County Code            object
County Name            object
District Code         float64
District Name          object
Position               object
White                  object
%White                float64
Black                 float64
%Black                float64
Hispanic              float64
%Hispanic             float64
Asian                 float64
%Asian                float64
Native American       float64
%Native American      float64
Hawaiian Native       float64
%Hawaiian Native      float64
Two or More Races     float64
%Two or More Races    float64
dtype: object

In [40]:
df2 = df2[df2['Position'] == 'Teacher'] # I only want to know the condition of teachers

In [41]:
df2

County Code County Name  District Code  \
558          07      Camden          150.0   
562          07      Camden          190.0   
566          07      Camden          260.0   
570          07      Camden          330.0   
574          07      Camden          340.0   
578          07      Camden          390.0   
582          07      Camden          580.0   
586          07      Camden          680.0   
590          07      Camden          695.0   
594          07      Camden          700.0   
598          07      Camden          800.0   
602          07      Camden          880.0   
606          07      Camden          940.0   
610          07      Camden         1255.0   
614          07      Camden         1720.0   
618          07      Camden         1770.0   
622          07      Camden         1780.0   
626          07      Camden         1799.0   
630          07      Camden         1801.0   
634          07      Camden         1802.0   
638          07      Camden         1880.0   
642          07      Camden         1890.0   
646          07      Camden         1900.0   
650          07      Camden         2540.0   
654          07      Camden         2560.0   
658          07      Camden         2670.0   
662          07      Camden         2890.0   
666          07      Camden         3110.0   
670          07      Camden         3420.0   
674          07      Camden         3770.0   
678          07      Camden         4060.0   
682          07      Camden         4110.0   
686          07      Camden         4590.0   
690          07      Camden         4790.0   
694          07      Camden         5035.0   
698          07      Camden         5080.0   
702          07      Camden         5400.0   
706          07      Camden         5560.0   
710          07      Camden         5820.0   
714          07      Camden         5900.0   

                                         District Name Position  White  \
558                     Audubon Public School District  Teacher  119.2   
562                         Barrington School District  Teacher   58.8   
566                    Bellmawr Public School District  Teacher   97.0   
570                     Berlin Borough School District  Teacher   75.6   
574                    Berlin Township School District  Teacher   52.1   
578          Black Horse Pike Regional School District  Teacher  268.9   
582                   Brooklawn Public School District  Teacher   29.4   
586                        Camden City School District  Teacher  303.5   
590      Camden County Educational Services Commission  Teacher    0.0   
594            Camden County Technical School District  Teacher  160.6   
598                        Cherry Hill School District  Teacher  788.8   
602               Clementon Elementary School District  Teacher   48.2   
606                Collingswood Public School District  Teacher  183.7   
610     Eastern Camden County Regional School District  Teacher  127.0   
614               Gibbsboro Elementary School District  Teacher   27.0   
618             Gloucester City Public School District  Teacher  168.8   
622                 Gloucester Township Public Schools  Teacher  497.5   
626  Kipp: Cooper Norcross A New Jersey Nonprofit C...  Teacher   32.0   
630                                   Camden Prep Inc.  Teacher    0.5   
634                     Mastery Schools Of Camden Inc.  Teacher  113.5   
638                     Haddon Heights School District  Teacher  126.7   
642                    Haddon Township School District  Teacher  146.7   
646                        Haddonfield School District  Teacher  206.9   
650                     Laurel Springs School District  Teacher   14.6   
654                            Lawnside School Distric  Teacher   11.0   
658                  Lindenwold Public School District  Teacher  199.0   
662                           Magnolia School District  Teacher   36.7   
666                      Merchantville School

# 3. Merge

In [115]:
mergedOuter = pd.merge(df1, df2, how='outer', on=['County Code', 'County Name', 'District Name'],indicator=True)
mergedOuter

County Code County Name District Code_x  \
0           07      Camden            0150   
1           07      Camden            0190   
2           07      Camden            0260   
3           07      Camden            0330   
4           07      Camden            0340   
5           07      Camden            0390   
6           07      Camden            0580   
7           07      Camden            0680   
8           07      Camden            0700   
9           07      Camden            0800   
10          07      Camden            0880   
11          07      Camden            0940   
12          07      Camden            1255   
13          07      Camden            1720   
14          07      Camden            1770   
15          07      Camden            1780   
16          07      Camden            1799   
17          07      Camden            1801   
18          07      Camden            1802   
19          07      Camden            1880   
20          07      Camden            1890   
21          07      Camden            1900   
22          07      Camden            2540   
23          07      Camden            2560   
24          07      Camden            2670   
25          07      Camden            2890   
26          07      Camden            3110   
27          07      Camden            3420   
28          07      Camden            3770   
29          07      Camden            4060   
30          07      Camden            4110   
31          07      Camden            4590   
32          07      Camden            4790   
33          07      Camden            5035   
34          07      Camden            5080   
35          07      Camden            5400   
36          07      Camden            5560   
37          07      Camden            5820   
38          07      Camden            5900   
39          07      Camden             NaN   

                                        District Name Total Enrollment  \
0                      Audubon Public School District             1444   
1                          Barrington School District              563   
2                     Bellmawr Public School District             1166   
3                      Berlin Borough School District              807   
4                     Berlin Township School District              604   
5           Black Horse Pike Regional School District             3478   
6                    Brooklawn Public School District              285   
7                         Camden City School District             7343   
8             Camden County Technical School District             2245   
9                         Cherry Hill School District            10469   
10               Clementon Elementary School District              516   
11                Collingswood Public School District             2200   
12     Eastern Camden County Regional School District             1926   
13               Gibbsboro Elementary School District              276   
14             Gloucester City Public School District             2220   
15                 Gloucester Township Public Schools             6368   
16  Kipp: Cooper Norcross A New Jersey Nonprofit C...             1775   
17                                   Camden Prep Inc.              949   
18                     Mastery Schools Of Camden Inc.             2737   
19                     Haddon Heights School District             1514   
20                    Haddon Township School District             1971   
21                        Haddonfield School District             2645   
22                     Laurel Springs School District              167   
23                            Lawnside School Distric              308   
24                  Lindenwold Public School District             2926   
25                           Magnolia School District              375   
26                      Merchantville School District              403   
27                        Mt. Ephraim School

In [116]:
mergedOuter['_merge'].value_counts()
mergedOuter['District Name'][mergedOuter['_merge']=='left_only']
mergedOuter['District Name'][mergedOuter['_merge']=='right_only']

both          39
right_only     1
left_only      0
Name: _merge, dtype: int64

Series([], Name: District Name, dtype: object)

39    Camden County Educational Services Commission
Name: District Name, dtype: object

I googled Camden County Educational Services Commission. It is not a school district but seems like a service agency. So it is normal that cannot be merged.

In [44]:
mergedInner = pd.merge(df1, df2, how='inner', on=['County Code', 'County Name', 'District Name'])
mergedInner

County Code County Name District Code_x  \
0           07      Camden            0150   
1           07      Camden            0190   
2           07      Camden            0260   
3           07      Camden            0330   
4           07      Camden            0340   
5           07      Camden            0390   
6           07      Camden            0580   
7           07      Camden            0680   
8           07      Camden            0700   
9           07      Camden            0800   
10          07      Camden            0880   
11          07      Camden            0940   
12          07      Camden            1255   
13          07      Camden            1720   
14          07      Camden            1770   
15          07      Camden            1780   
16          07      Camden            1799   
17          07      Camden            1801   
18          07      Camden            1802   
19          07      Camden            1880   
20          07      Camden            1890   
21          07      Camden            1900   
22          07      Camden            2540   
23          07      Camden            2560   
24          07      Camden            2670   
25          07      Camden            2890   
26          07      Camden            3110   
27          07      Camden            3420   
28          07      Camden            3770   
29          07      Camden            4060   
30          07      Camden            4110   
31          07      Camden            4590   
32          07      Camden            4790   
33          07      Camden            5035   
34          07      Camden            5080   
35          07      Camden            5400   
36          07      Camden            5560   
37          07      Camden            5820   
38          07      Camden            5900   

                                        District Name Total Enrollment  \
0                      Audubon Public School District             1444   
1                          Barrington School District              563   
2                     Bellmawr Public School District             1166   
3                      Berlin Borough School District              807   
4                     Berlin Township School District              604   
5           Black Horse Pike Regional School District             3478   
6                    Brooklawn Public School District              285   
7                         Camden City School District             7343   
8             Camden County Technical School District             2245   
9                         Cherry Hill School District            10469   
10               Clementon Elementary School District              516   
11                Collingswood Public School District             2200   
12     Eastern Camden County Regional School District             1926   
13               Gibbsboro Elementary School District              276   
14             Gloucester City Public School District             2220   
15                 Gloucester Township Public Schools             6368   
16  Kipp: Cooper Norcross A New Jersey Nonprofit C...             1775   
17                                   Camden Prep Inc.              949   
18                     Mastery Schools Of Camden Inc.             2737   
19                     Haddon Heights School District             1514   
20                    Haddon Township School District             1971   
21                        Haddonfield School District             2645   
22                     Laurel Springs School District              167   
23                            Lawnside School Distric              308   
24                  Lindenwold Public School District             2926   
25                           Magnolia School District              375   
26                      Merchantville School District              403   
27                        Mt. Ephraim School District              421   
28              

In [45]:
mergedLeft = pd.merge(df1, df2, how='left', on=['County Code', 'County Name', 'District Name'])
mergedLeft

County Code County Name District Code_x  \
0           07      Camden            0150   
1           07      Camden            0190   
2           07      Camden            0260   
3           07      Camden            0330   
4           07      Camden            0340   
5           07      Camden            0390   
6           07      Camden            0580   
7           07      Camden            0680   
8           07      Camden            0700   
9           07      Camden            0800   
10          07      Camden            0880   
11          07      Camden            0940   
12          07      Camden            1255   
13          07      Camden            1720   
14          07      Camden            1770   
15          07      Camden            1780   
16          07      Camden            1799   
17          07      Camden            1801   
18          07      Camden            1802   
19          07      Camden            1880   
20          07      Camden            1890   
21          07      Camden            1900   
22          07      Camden            2540   
23          07      Camden            2560   
24          07      Camden            2670   
25          07      Camden            2890   
26          07      Camden            3110   
27          07      Camden            3420   
28          07      Camden            3770   
29          07      Camden            4060   
30          07      Camden            4110   
31          07      Camden            4590   
32          07      Camden            4790   
33          07      Camden            5035   
34          07      Camden            5080   
35          07      Camden            5400   
36          07      Camden            5560   
37          07      Camden            5820   
38          07      Camden            5900   

                                        District Name Total Enrollment  \
0                      Audubon Public School District             1444   
1                          Barrington School District              563   
2                     Bellmawr Public School District             1166   
3                      Berlin Borough School District              807   
4                     Berlin Township School District              604   
5           Black Horse Pike Regional School District             3478   
6                    Brooklawn Public School District              285   
7                         Camden City School District             7343   
8             Camden County Technical School District             2245   
9                         Cherry Hill School District            10469   
10               Clementon Elementary School District              516   
11                Collingswood Public School District             2200   
12     Eastern Camden County Regional School District             1926   
13               Gibbsboro Elementary School District              276   
14             Gloucester City Public School District             2220   
15                 Gloucester Township Public Schools             6368   
16  Kipp: Cooper Norcross A New Jersey Nonprofit C...             1775   
17                                   Camden Prep Inc.              949   
18                     Mastery Schools Of Camden Inc.             2737   
19                     Haddon Heights School District             1514   
20                    Haddon Township School District             1971   
21                        Haddonfield School District             2645   
22                     Laurel Springs School District              167   
23                            Lawnside School Distric              308   
24                  Lindenwold Public School District             2926   
25                           Magnolia School District              375   
26                      Merchantville School District              403   
27                        Mt. Ephraim School District              421   
28              

In [46]:
mergedRight = pd.merge(df1, df2, how='right', on=['County Code', 'County Name', 'District Name'])
mergedRight

County Code County Name District Code_x  \
0           07      Camden            0150   
1           07      Camden            0190   
2           07      Camden            0260   
3           07      Camden            0330   
4           07      Camden            0340   
5           07      Camden            0390   
6           07      Camden            0580   
7           07      Camden            0680   
8           07      Camden             NaN   
9           07      Camden            0700   
10          07      Camden            0800   
11          07      Camden            0880   
12          07      Camden            0940   
13          07      Camden            1255   
14          07      Camden            1720   
15          07      Camden            1770   
16          07      Camden            1780   
17          07      Camden            1799   
18          07      Camden            1801   
19          07      Camden            1802   
20          07      Camden            1880   
21          07      Camden            1890   
22          07      Camden            1900   
23          07      Camden            2540   
24          07      Camden            2560   
25          07      Camden            2670   
26          07      Camden            2890   
27          07      Camden            3110   
28          07      Camden            3420   
29          07      Camden            3770   
30          07      Camden            4060   
31          07      Camden            4110   
32          07      Camden            4590   
33          07      Camden            4790   
34          07      Camden            5035   
35          07      Camden            5080   
36          07      Camden            5400   
37          07      Camden            5560   
38          07      Camden            5820   
39          07      Camden            5900   

                                        District Name Total Enrollment  \
0                      Audubon Public School District             1444   
1                          Barrington School District              563   
2                     Bellmawr Public School District             1166   
3                      Berlin Borough School District              807   
4                     Berlin Township School District              604   
5           Black Horse Pike Regional School District             3478   
6                    Brooklawn Public School District              285   
7                         Camden City School District             7343   
8       Camden County Educational Services Commission              NaN   
9             Camden County Technical School District             2245   
10                        Cherry Hill School District            10469   
11               Clementon Elementary School District              516   
12                Collingswood Public School District             2200   
13     Eastern Camden County Regional School District             1926   
14               Gibbsboro Elementary School District              276   
15             Gloucester City Public School District             2220   
16                 Gloucester Township Public Schools             6368   
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...             1775   
18                                   Camden Prep Inc.              949   
19                     Mastery Schools Of Camden Inc.             2737   
20                     Haddon Heights School District             1514   
21                    Haddon Township School District             1971   
22                        Haddonfield School District             2645   
23                     Laurel Springs School District              167   
24                            Lawnside School Distric              308   
25                  Lindenwold Public School District             2926   
26                           Magnolia School District              375   
27                      Merchantville School

In [47]:
df3=mergedRight
df3

County Code County Name District Code_x  \
0           07      Camden            0150   
1           07      Camden            0190   
2           07      Camden            0260   
3           07      Camden            0330   
4           07      Camden            0340   
5           07      Camden            0390   
6           07      Camden            0580   
7           07      Camden            0680   
8           07      Camden             NaN   
9           07      Camden            0700   
10          07      Camden            0800   
11          07      Camden            0880   
12          07      Camden            0940   
13          07      Camden            1255   
14          07      Camden            1720   
15          07      Camden            1770   
16          07      Camden            1780   
17          07      Camden            1799   
18          07      Camden            1801   
19          07      Camden            1802   
20          07      Camden            1880   
21          07      Camden            1890   
22          07      Camden            1900   
23          07      Camden            2540   
24          07      Camden            2560   
25          07      Camden            2670   
26          07      Camden            2890   
27          07      Camden            3110   
28          07      Camden            3420   
29          07      Camden            3770   
30          07      Camden            4060   
31          07      Camden            4110   
32          07      Camden            4590   
33          07      Camden            4790   
34          07      Camden            5035   
35          07      Camden            5080   
36          07      Camden            5400   
37          07      Camden            5560   
38          07      Camden            5820   
39          07      Camden            5900   

                                        District Name Total Enrollment  \
0                      Audubon Public School District             1444   
1                          Barrington School District              563   
2                     Bellmawr Public School District             1166   
3                      Berlin Borough School District              807   
4                     Berlin Township School District              604   
5           Black Horse Pike Regional School District             3478   
6                    Brooklawn Public School District              285   
7                         Camden City School District             7343   
8       Camden County Educational Services Commission              NaN   
9             Camden County Technical School District             2245   
10                        Cherry Hill School District            10469   
11               Clementon Elementary School District              516   
12                Collingswood Public School District             2200   
13     Eastern Camden County Regional School District             1926   
14               Gibbsboro Elementary School District              276   
15             Gloucester City Public School District             2220   
16                 Gloucester Township Public Schools             6368   
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...             1775   
18                                   Camden Prep Inc.              949   
19                     Mastery Schools Of Camden Inc.             2737   
20                     Haddon Heights School District             1514   
21                    Haddon Township School District             1971   
22                        Haddonfield School District             2645   
23                     Laurel Springs School District              167   
24                            Lawnside School Distric              308   
25                  Lindenwold Public School District             2926   
26                           Magnolia School District              375   
27                      Merchantville School

In [48]:
df3.drop(['District Code_x', 'District Code_y'], axis=1)

County Code County Name                                      District Name  \
0           07      Camden                     Audubon Public School District   
1           07      Camden                         Barrington School District   
2           07      Camden                    Bellmawr Public School District   
3           07      Camden                     Berlin Borough School District   
4           07      Camden                    Berlin Township School District   
5           07      Camden          Black Horse Pike Regional School District   
6           07      Camden                   Brooklawn Public School District   
7           07      Camden                        Camden City School District   
8           07      Camden      Camden County Educational Services Commission   
9           07      Camden            Camden County Technical School District   
10          07      Camden                        Cherry Hill School District   
11          07      Camden               Clementon Elementary School District   
12          07      Camden                Collingswood Public School District   
13          07      Camden     Eastern Camden County Regional School District   
14          07      Camden               Gibbsboro Elementary School District   
15          07      Camden             Gloucester City Public School District   
16          07      Camden                 Gloucester Township Public Schools   
17          07      Camden  Kipp: Cooper Norcross A New Jersey Nonprofit C...   
18          07      Camden                                   Camden Prep Inc.   
19          07      Camden                     Mastery Schools Of Camden Inc.   
20          07      Camden                     Haddon Heights School District   
21          07      Camden                    Haddon Township School District   
22          07      Camden                        Haddonfield School District   
23          07      Camden                     Laurel Springs School District   
24          07      Camden                            Lawnside School Distric   
25          07      Camden                  Lindenwold Public School District   
26          07      Camden                           Magnolia School District   
27          07      Camden                      Merchantville School District   
28          07      Camden                        Mt. Ephraim School District   
29          07      Camden                      Oaklyn Public School District   
30          07      Camden  Pennsauken Township Board Of Education School ...   
31          07      Camden                          Pine Hill School District   
32          07      Camden                   Runnemede Public School District   
33          07      Camden                          Somerdale School District   
34          07      Camden                  Sterling Regional School District   
35          07      Camden                          Stratford School District   
36          07      Camden                  Voorhees Township School District   
37          07      Camden                 Waterford Township School District   
38          07      Camden                   Winslow Township School District   
39          07      Camden                          Woodlynne School District   

   Total Enrollment White_x %White_x Black_x %Black_x Hispanic_x %Hispanic_x  \
0              1444    1235     85.5      47      3.3        109         7.5   
1               563     432     76.7      29      5.2         48         8.5   
2              1166     671     57.5      48      4.1        256          22   
3               807     659     81.7      57      7.1         26         3.2   
4               604     356     58.9      73     12.1        114        18.9   
5              3478    1840     52.9     914     26.3        391        11.2   
6               285     157     55.1      41     14.4         52        18.2   
7              7343      68      0.9    3

In [49]:
df3.dtypes

County Code              object
County Name              object
District Code_x          object
District Name            object
Total Enrollment         object
White_x                  object
%White_x                 object
Black_x                  object
%Black_x                 object
Hispanic_x               object
%Hispanic_x              object
Asian_x                  object
%Asian_x                 object
Native American_x        object
%Native American_x       object
Hawaiian Native_x        object
%Hawaiian Native_x       object
Two or More Races_x      object
%Two or More Races_x     object
District Code_y         float64
Position                 object
White_y                  object
%White_y                float64
Black_y                 float64
%Black_y                float64
Hispanic_y              float64
%Hispanic_y             float64
Asian_y                 float64
%Asian_y                float64
Native American_y       float64
%Native American_y      float64
Hawaiian

Variables ended by x are data of students, and variables ended by y are data of teachers.

# 4. Data management

In [60]:
df3.dtypes

County Code              object
County Name              object
District Code_x          object
District Name            object
Total Enrollment         object
White_x                  object
%White_x                 object
Black_x                  object
%Black_x                 object
Hispanic_x               object
%Hispanic_x              object
Asian_x                  object
%Asian_x                 object
Native American_x        object
%Native American_x       object
Hawaiian Native_x        object
%Hawaiian Native_x       object
Two or More Races_x      object
%Two or More Races_x     object
District Code_y         float64
Position                 object
White_y                  object
%White_y                float64
Black_y                 float64
%Black_y                float64
Hispanic_y              float64
%Hispanic_y             float64
Asian_y                 float64
%Asian_y                float64
Native American_y       float64
%Native American_y      float64
Hawaiian

In [63]:
df3['enr']=df3["Total Enrollment"].astype(float) # To transfer object to float

In [64]:
df3.dtypes

County Code              object
County Name              object
District Code_x          object
District Name            object
Total Enrollment         object
White_x                  object
%White_x                 object
Black_x                  object
%Black_x                 object
Hispanic_x               object
%Hispanic_x              object
Asian_x                  object
%Asian_x                 object
Native American_x        object
%Native American_x       object
Hawaiian Native_x        object
%Hawaiian Native_x       object
Two or More Races_x      object
%Two or More Races_x     object
District Code_y         float64
Position                 object
White_y                  object
%White_y                float64
Black_y                 float64
%Black_y                float64
Hispanic_y              float64
%Hispanic_y             float64
Asian_y                 float64
%Asian_y                float64
Native American_y       float64
%Native American_y      float64
Hawaiian

In [91]:
df3['White students']=df3['%White_x'].astype(float)

In [92]:
df3['Black students']=df3['%Black_x'].astype(float)

In [93]:
df3['Hispanic students']=df3['%Hispanic_x'].astype(float)

In [94]:
df3[['White students','%White_x']]

White students %White_x
0             85.5     85.5
1             76.7     76.7
2             57.5     57.5
3             81.7     81.7
4             58.9     58.9
5             52.9     52.9
6             55.1     55.1
7              0.9      0.9
8              NaN      NaN
9             29.6     29.6
10            55.2     55.2
11            33.7     33.7
12            60.1     60.1
13            59.4     59.4
14            64.1     64.1
15            61.8     61.8
16            48.3     48.3
17             0.3      0.3
18             0.1      0.1
19             0.4      0.4
20            74.7     74.7
21            80.0       80
22            87.5     87.5
23            64.1     64.1
24             1.3      1.3
25             7.5      7.5
26            50.1     50.1
27            56.1     56.1
28            81.9     81.9
29            76.9     76.9
30             9.4      9.4
31            39.9     39.9
32            78.0       78
33            39.7     39.7
34            56.1     56.1
35            59.0       59
36            50.6     50.6
37            77.9     77.9
38            19.1     19.1
39             2.3      2.3

In [95]:
df3['White students'].mask(df3['White students'] >=80 ,'White Majority', inplace=True)
df3['Black students'].mask(df3['Black students'] >=70 ,'Black Majority', inplace=True)
df3['Hispanic students'].mask(df3['Hispanic students'] >=60 ,'Hispanic Majority', inplace=True)
df3 # It is very interesting. At the beginning I use >=80 for all the three variables, finding that there are no school districts in Camden County have more than 80% Black or Hispanic students

County Code County Name District Code_x  \
0           07      Camden            0150   
1           07      Camden            0190   
2           07      Camden            0260   
3           07      Camden            0330   
4           07      Camden            0340   
5           07      Camden            0390   
6           07      Camden            0580   
7           07      Camden            0680   
8           07      Camden             NaN   
9           07      Camden            0700   
10          07      Camden            0800   
11          07      Camden            0880   
12          07      Camden            0940   
13          07      Camden            1255   
14          07      Camden            1720   
15          07      Camden            1770   
16          07      Camden            1780   
17          07      Camden            1799   
18          07      Camden            1801   
19          07      Camden            1802   
20          07      Camden            1880   
21          07      Camden            1890   
22          07      Camden            1900   
23          07      Camden            2540   
24          07      Camden            2560   
25          07      Camden            2670   
26          07      Camden            2890   
27          07      Camden            3110   
28          07      Camden            3420   
29          07      Camden            3770   
30          07      Camden            4060   
31          07      Camden            4110   
32          07      Camden            4590   
33          07      Camden            4790   
34          07      Camden            5035   
35          07      Camden            5080   
36          07      Camden            5400   
37          07      Camden            5560   
38          07      Camden            5820   
39          07      Camden            5900   

                                        District Name Total Enrollment  \
0                      Audubon Public School District             1444   
1                          Barrington School District              563   
2                     Bellmawr Public School District             1166   
3                      Berlin Borough School District              807   
4                     Berlin Township School District              604   
5           Black Horse Pike Regional School District             3478   
6                    Brooklawn Public School District              285   
7                         Camden City School District             7343   
8       Camden County Educational Services Commission              NaN   
9             Camden County Technical School District             2245   
10                        Cherry Hill School District            10469   
11               Clementon Elementary School District              516   
12                Collingswood Public School District             2200   
13     Eastern Camden County Regional School District             1926   
14               Gibbsboro Elementary School District              276   
15             Gloucester City Public School District             2220   
16                 Gloucester Township Public Schools             6368   
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...             1775   
18                                   Camden Prep Inc.              949   
19                     Mastery Schools Of Camden Inc.             2737   
20                     Haddon Heights School District             1514   
21                    Haddon Township School District             1971   
22                        Haddonfield School District             2645   
23                     Laurel Springs School District              167   
24                            Lawnside School Distric              308   
25                  Lindenwold Public School District             2926   
26                           Magnolia School District              375   
27                      Merchantville School

In [97]:
df3[['District Name', 'Black_x', 'Black_y']]

District Name Black_x  Black_y
0                      Audubon Public School District      47      0.0
1                          Barrington School District      29      0.0
2                     Bellmawr Public School District      48      1.0
3                      Berlin Borough School District      57      0.0
4                     Berlin Township School District      73      1.0
5           Black Horse Pike Regional School District     914     10.0
6                    Brooklawn Public School District      41      0.0
7                         Camden City School District    3134    270.5
8       Camden County Educational Services Commission     NaN      0.0
9             Camden County Technical School District     538     18.0
10                        Cherry Hill School District     921     39.8
11               Clementon Elementary School District     115      1.0
12                Collingswood Public School District     247      9.0
13     Eastern Camden County Regional School District     221      4.0
14               Gibbsboro Elementary School District      27      0.0
15             Gloucester City Public School District     251      2.0
16                 Gloucester Township Public Schools    1663     16.7
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...     985     26.0
18                                   Camden Prep Inc.     737      0.3
19                     Mastery Schools Of Camden Inc.     765     56.0
20                     Haddon Heights School District     145      3.0
21                    Haddon Township School District      62      0.0
22                        Haddonfield School District      38      3.0
23                     Laurel Springs School District      25      0.0
24                            Lawnside School Distric     228     15.0
25                  Lindenwold Public School District     960     35.5
26                           Magnolia School District      67      1.0
27                      Merchantville School District      49      1.8
28                        Mt. Ephraim School District      18      0.0
29                      Oaklyn Public School District      14      0.0
30  Pennsauken Township Board Of Education School ...    1134     43.0
31                          Pine Hill School District     581      8.0
32                   Runnemede Public School District      42      1.0
33                          Somerdale School District     111      1.0
34                  Sterling Regional School District     180      4.0
35                          Stratford School District     113      1.5
36                  Voorhees Township School District     303      3.0
37                 Waterford Township School District      28      1.0
38                   Winslow Township School District    2572     63.5
39                          Woodlynne School District      87      2.0

In [98]:
df3[['District Name', '%Black_x', '%Black_y']]

District Name %Black_x  %Black_y
0                      Audubon Public School District      3.3       0.0
1                          Barrington School District      5.2       0.0
2                     Bellmawr Public School District      4.1       1.0
3                      Berlin Borough School District      7.1       0.0
4                     Berlin Township School District     12.1       1.8
5           Black Horse Pike Regional School District     26.3       3.5
6                    Brooklawn Public School District     14.4       0.0
7                         Camden City School District     42.7      40.5
8       Camden County Educational Services Commission      NaN       0.0
9             Camden County Technical School District       24       9.4
10                        Cherry Hill School District      8.8       4.4
11               Clementon Elementary School District     22.3       2.0
12                Collingswood Public School District     11.2       4.5
13     Eastern Camden County Regional School District     11.5       2.9
14               Gibbsboro Elementary School District      9.8       0.0
15             Gloucester City Public School District     11.3       1.2
16                 Gloucester Township Public Schools     26.1       3.1
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...     55.5      32.5
18                                   Camden Prep Inc.     77.7      33.3
19                     Mastery Schools Of Camden Inc.       28      29.9
20                     Haddon Heights School District      9.6       2.3
21                    Haddon Township School District      3.1       0.0
22                        Haddonfield School District      1.4       1.4
23                     Laurel Springs School District       15       0.0
24                            Lawnside School Distric       74      57.7
25                  Lindenwold Public School District     32.8      13.2
26                           Magnolia School District     17.9       2.7
27                      Merchantville School District     12.2       5.8
28                        Mt. Ephraim School District      4.3       0.0
29                      Oaklyn Public School District      5.1       0.0
30  Pennsauken Township Board Of Education School ...     24.4      11.1
31                          Pine Hill School District     32.2       4.7
32                   Runnemede Public School District        5       1.4
33                          Somerdale School District     24.2       2.3
34                  Sterling Regional School District     19.7       5.8
35                          Stratford School District     13.2       2.2
36                  Voorhees Township School District     10.4       1.3
37                 Waterford Township School District      3.3       1.2
38                   Winslow Township School District     55.8      14.1
39                          Woodlynne School District     22.1       6.0

Research found that for a Black student, it is better for his/her growth if he/she had a teacher of the same race. And this phenomenon is even more obvious for male students. From the Camden County data, it is obvious that for many districts have high rate of Black students, there are not enough same race teachers work with them. But Camden City School District performed well in this respect. Mastery Schools Of Camden Inc. performed well, too. This finding indicates that it is necessary to improve the diversity of teachers in public schools.

In [99]:
df3[['District Name', 'Asian_x', 'Asian_y']]

District Name Asian_x  Asian_y
0                      Audubon Public School District      16      2.0
1                          Barrington School District      24      1.0
2                     Bellmawr Public School District     130      0.0
3                      Berlin Borough School District      29      0.0
4                     Berlin Township School District      52      1.0
5           Black Horse Pike Regional School District     227      0.0
6                    Brooklawn Public School District      13      0.0
7                         Camden City School District      69     16.0
8       Camden County Educational Services Commission     NaN      0.0
9             Camden County Technical School District      77      2.0
10                        Cherry Hill School District    1821     31.0
11               Clementon Elementary School District       9      0.0
12                Collingswood Public School District      56      2.8
13     Eastern Camden County Regional School District     269      2.0
14               Gibbsboro Elementary School District      17      0.0
15             Gloucester City Public School District     113      1.0
16                 Gloucester Township Public Schools     296      0.0
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...       1      1.0
18                                   Camden Prep Inc.       1      0.0
19                     Mastery Schools Of Camden Inc.      18      1.0
20                     Haddon Heights School District      31      1.0
21                    Haddon Township School District      63      1.0
22                        Haddonfield School District      97      5.0
23                     Laurel Springs School District       0      0.0
24                            Lawnside School Distric       3      0.0
25                  Lindenwold Public School District      37      2.0
26                           Magnolia School District      11      0.0
27                      Merchantville School District      13      0.0
28                        Mt. Ephraim School District       6      0.0
29                      Oaklyn Public School District      13      0.0
30  Pennsauken Township Board Of Education School ...     515      0.0
31                          Pine Hill School District      48      1.0
32                   Runnemede Public School District      21      1.0
33                          Somerdale School District      27      0.0
34                  Sterling Regional School District      39      0.0
35                          Stratford School District      44      0.0
36                  Voorhees Township School District     698      2.0
37                 Waterford Township School District       5      0.0
38                   Winslow Township School District     113      8.0
39                          Woodlynne School District      29      0.0

In [100]:
df3[['District Name', '%Asian_x', '%Asian_y']]

District Name %Asian_x  %Asian_y
0                      Audubon Public School District      1.1       1.6
1                          Barrington School District      4.3       1.6
2                     Bellmawr Public School District     11.1       0.0
3                      Berlin Borough School District      3.6       0.0
4                     Berlin Township School District      8.6       1.8
5           Black Horse Pike Regional School District      6.5       0.0
6                    Brooklawn Public School District      4.6       0.0
7                         Camden City School District      0.9       2.4
8       Camden County Educational Services Commission      NaN       0.0
9             Camden County Technical School District      3.4       1.0
10                        Cherry Hill School District     17.4       3.4
11               Clementon Elementary School District      1.7       0.0
12                Collingswood Public School District      2.5       1.4
13     Eastern Camden County Regional School District       14       1.4
14               Gibbsboro Elementary School District      6.2       0.0
15             Gloucester City Public School District      5.1       0.6
16                 Gloucester Township Public Schools      4.6       0.0
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...      0.1       1.3
18                                   Camden Prep Inc.      0.1       0.0
19                     Mastery Schools Of Camden Inc.      0.7       0.5
20                     Haddon Heights School District        2       0.8
21                    Haddon Township School District      3.2       0.7
22                        Haddonfield School District      3.7       2.3
23                     Laurel Springs School District        0       0.0
24                            Lawnside School Distric        1       0.0
25                  Lindenwold Public School District      1.3       0.7
26                           Magnolia School District      2.9       0.0
27                      Merchantville School District      3.2       0.0
28                        Mt. Ephraim School District      1.4       0.0
29                      Oaklyn Public School District      4.7       0.0
30  Pennsauken Township Board Of Education School ...     11.1       0.0
31                          Pine Hill School District      2.7       0.6
32                   Runnemede Public School District      2.5       1.4
33                          Somerdale School District      5.9       0.0
34                  Sterling Regional School District      4.3       0.0
35                          Stratford School District      5.1       0.0
36                  Voorhees Township School District       24       0.8
37                 Waterford Township School District      0.6       0.0
38                   Winslow Township School District      2.5       1.8
39                          Woodlynne School District      7.4       0.0

In [111]:
df3[['District Name', 'White_x', 'White_y']]

District Name White_x White_y
0                      Audubon Public School District    1235   119.2
1                          Barrington School District     432    58.8
2                     Bellmawr Public School District     671    97.0
3                      Berlin Borough School District     659    75.6
4                     Berlin Township School District     356    52.1
5           Black Horse Pike Regional School District    1840   268.9
6                    Brooklawn Public School District     157    29.4
7                         Camden City School District      68   303.5
8       Camden County Educational Services Commission     NaN     0.0
9             Camden County Technical School District     664   160.6
10                        Cherry Hill School District    5774   788.8
11               Clementon Elementary School District     174    48.2
12                Collingswood Public School District    1323   183.7
13     Eastern Camden County Regional School District    1144   127.0
14               Gibbsboro Elementary School District     177    27.0
15             Gloucester City Public School District    1372   168.8
16                 Gloucester Township Public Schools    3076   497.5
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...       5    32.0
18                                   Camden Prep Inc.       1     0.5
19                     Mastery Schools Of Camden Inc.      10   113.5
20                     Haddon Heights School District    1131   126.7
21                    Haddon Township School District    1576   146.7
22                        Haddonfield School District    2315   206.9
23                     Laurel Springs School District     107    14.6
24                            Lawnside School Distric       4    11.0
25                  Lindenwold Public School District     219   199.0
26                           Magnolia School District     188    36.7
27                      Merchantville School District     226    27.8
28                        Mt. Ephraim School District     345    40.6
29                      Oaklyn Public School District     213    27.8
30  Pennsauken Township Board Of Education School ...     437   313.0
31                          Pine Hill School District     721   153.1
32                   Runnemede Public School District     653    70.5
33                          Somerdale School District     182    42.8
34                  Sterling Regional School District     512    64.0
35                          Stratford School District     506    65.5
36                  Voorhees Township School District    1474   232.7
37                 Waterford Township School District     667    84.1
38                   Winslow Township School District     880   359.5
39                          Woodlynne School District       9    31.1

In [110]:
df3[['District Name', '%White_x', '%White_y']]

District Name %White_x  %White_y
0                      Audubon Public School District     85.5      97.5
1                          Barrington School District     76.7      96.7
2                     Bellmawr Public School District     57.5      96.0
3                      Berlin Borough School District     81.7     100.0
4                     Berlin Township School District     58.9      94.6
5           Black Horse Pike Regional School District     52.9      93.1
6                    Brooklawn Public School District     55.1     100.0
7                         Camden City School District      0.9      45.4
8       Camden County Educational Services Commission      NaN       0.0
9             Camden County Technical School District     29.6      84.3
10                        Cherry Hill School District     55.2      87.2
11               Clementon Elementary School District     33.7      96.0
12                Collingswood Public School District     60.1      91.4
13     Eastern Camden County Regional School District     59.4      92.0
14               Gibbsboro Elementary School District     64.1     100.0
15             Gloucester City Public School District     61.8      97.7
16                 Gloucester Township Public Schools     48.3      93.1
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...      0.3      40.0
18                                   Camden Prep Inc.      0.1      55.6
19                     Mastery Schools Of Camden Inc.      0.4      60.5
20                     Haddon Heights School District     74.7      95.8
21                    Haddon Township School District       80      98.3
22                        Haddonfield School District     87.5      93.7
23                     Laurel Springs School District     64.1     100.0
24                            Lawnside School Distric      1.3      42.3
25                  Lindenwold Public School District      7.5      73.8
26                           Magnolia School District     50.1      97.3
27                      Merchantville School District     56.1      89.4
28                        Mt. Ephraim School District     81.9     100.0
29                      Oaklyn Public School District     76.9     100.0
30  Pennsauken Township Board Of Education School ...      9.4      81.1
31                          Pine Hill School District     39.9      90.5
32                   Runnemede Public School District       78      95.9
33                          Somerdale School District     39.7      97.7
34                  Sterling Regional School District     56.1      92.8
35                          Stratford School District       59      97.8
36                  Voorhees Township School District     50.6      97.5
37                 Waterford Township School District     77.9      97.7
38                   Winslow Township School District     19.1      80.1
39                          Woodlynne School District      2.3      94.0

In [112]:
df3[['District Name', 'Hispanic_x', 'Hispanic_y']]

District Name Hispanic_x  Hispanic_y
0                      Audubon Public School District        109         1.0
1                          Barrington School District         48         1.0
2                     Bellmawr Public School District        256         3.0
3                      Berlin Borough School District         26         0.0
4                     Berlin Township School District        114         1.0
5           Black Horse Pike Regional School District        391         7.0
6                    Brooklawn Public School District         52         0.0
7                         Camden City School District       4006        76.0
8       Camden County Educational Services Commission        NaN         0.0
9             Camden County Technical School District        884        10.0
10                        Cherry Hill School District       1414        43.0
11               Clementon Elementary School District        198         1.0
12                Collingswood Public School District        450         4.5
13     Eastern Camden County Regional School District        195         5.0
14               Gibbsboro Elementary School District         42         0.0
15             Gloucester City Public School District        451         1.0
16                 Gloucester Township Public Schools        947        13.2
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...        721        21.0
18                                   Camden Prep Inc.        210         0.0
19                     Mastery Schools Of Camden Inc.       1869        14.0
20                     Haddon Heights School District        142         1.7
21                    Haddon Township School District        191         1.6
22                        Haddonfield School District         87         5.0
23                     Laurel Springs School District         26         0.0
24                            Lawnside School Distric         53         0.0
25                  Lindenwold Public School District       1659        30.0
26                           Magnolia School District         79         0.0
27                      Merchantville School District         94         1.5
28                        Mt. Ephraim School District         40         0.0
29                      Oaklyn Public School District         29         0.0
30  Pennsauken Township Board Of Education School ...       2433        22.0
31                          Pine Hill School District        364         5.0
32                   Runnemede Public School District         82         0.0
33                          Somerdale School District        101         0.0
34                  Sterling Regional School District        143         1.0
35                          Stratford School District        158         0.0
36                  Voorhees Township School District        265         1.0
37                 Waterford Township School District        102         1.0
38                   Winslow Township School District        818        16.0
39                          Woodlynne School District        262         0.0

In [113]:
df3[['District Name', '%Hispanic_x', '%Hispanic_y']]

District Name %Hispanic_x  %Hispanic_y
0                      Audubon Public School District         7.5          0.8
1                          Barrington School District         8.5          1.6
2                     Bellmawr Public School District          22          3.0
3                      Berlin Borough School District         3.2          0.0
4                     Berlin Township School District        18.9          1.8
5           Black Horse Pike Regional School District        11.2          2.4
6                    Brooklawn Public School District        18.2          0.0
7                         Camden City School District        54.6         11.4
8       Camden County Educational Services Commission         NaN          0.0
9             Camden County Technical School District        39.4          5.2
10                        Cherry Hill School District        13.5          4.8
11               Clementon Elementary School District        38.4          2.0
12                Collingswood Public School District        20.5          2.2
13     Eastern Camden County Regional School District        10.1          3.6
14               Gibbsboro Elementary School District        15.2          0.0
15             Gloucester City Public School District        20.3          0.6
16                 Gloucester Township Public Schools        14.9          2.5
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...        40.6         26.3
18                                   Camden Prep Inc.        22.1          0.0
19                     Mastery Schools Of Camden Inc.        68.3          7.5
20                     Haddon Heights School District         9.4          1.3
21                    Haddon Township School District         9.7          1.1
22                        Haddonfield School District         3.3          2.3
23                     Laurel Springs School District        15.6          0.0
24                            Lawnside School Distric        17.2          0.0
25                  Lindenwold Public School District        56.7         11.1
26                           Magnolia School District        21.1          0.0
27                      Merchantville School District        23.3          4.8
28                        Mt. Ephraim School District         9.5          0.0
29                      Oaklyn Public School District        10.5          0.0
30  Pennsauken Township Board Of Education School ...        52.3          5.7
31                          Pine Hill School District        20.1          3.0
32                   Runnemede Public School District         9.8          0.0
33                          Somerdale School District          22          0.0
34                  Sterling Regional School District        15.7          1.4
35                          Stratford School District        18.4          0.0
36                  Voorhees Township School District         9.1          0.4
37                 Waterford Township School District        11.9          1.2
38                   Winslow Township School District        17.8          3.6
39                          Woodlynne School District        66.7          0.0

In [114]:
df3[['District Name', '%Black_x', '%White_y']]

District Name %Black_x  %White_y
0                      Audubon Public School District      3.3      97.5
1                          Barrington School District      5.2      96.7
2                     Bellmawr Public School District      4.1      96.0
3                      Berlin Borough School District      7.1     100.0
4                     Berlin Township School District     12.1      94.6
5           Black Horse Pike Regional School District     26.3      93.1
6                    Brooklawn Public School District     14.4     100.0
7                         Camden City School District     42.7      45.4
8       Camden County Educational Services Commission      NaN       0.0
9             Camden County Technical School District       24      84.3
10                        Cherry Hill School District      8.8      87.2
11               Clementon Elementary School District     22.3      96.0
12                Collingswood Public School District     11.2      91.4
13     Eastern Camden County Regional School District     11.5      92.0
14               Gibbsboro Elementary School District      9.8     100.0
15             Gloucester City Public School District     11.3      97.7
16                 Gloucester Township Public Schools     26.1      93.1
17  Kipp: Cooper Norcross A New Jersey Nonprofit C...     55.5      40.0
18                                   Camden Prep Inc.     77.7      55.6
19                     Mastery Schools Of Camden Inc.       28      60.5
20                     Haddon Heights School District      9.6      95.8
21                    Haddon Township School District      3.1      98.3
22                        Haddonfield School District      1.4      93.7
23                     Laurel Springs School District       15     100.0
24                            Lawnside School Distric       74      42.3
25                  Lindenwold Public School District     32.8      73.8
26                           Magnolia School District     17.9      97.3
27                      Merchantville School District     12.2      89.4
28                        Mt. Ephraim School District      4.3     100.0
29                      Oaklyn Public School District      5.1     100.0
30  Pennsauken Township Board Of Education School ...     24.4      81.1
31                          Pine Hill School District     32.2      90.5
32                   Runnemede Public School District        5      95.9
33                          Somerdale School District     24.2      97.7
34                  Sterling Regional School District     19.7      92.8
35                          Stratford School District     13.2      97.8
36                  Voorhees Township School District     10.4      97.5
37                 Waterford Township School District      3.3      97.7
38                   Winslow Township School District     55.8      80.1
39                          Woodlynne School District     22.1      94.0

In [106]:
df3[['%White_x','%Black_x','%Hispanic_x','%Asian_x','District Name']].groupby('District Name').describe()

%White_x                    \
                                                      count unique   top freq   
District Name                                                                   
Audubon Public School District                            1      1  85.5    1   
Barrington School District                                1      1  76.7    1   
Bellmawr Public School District                           1      1  57.5    1   
Berlin Borough School District                            1      1  81.7    1   
Berlin Township School District                           1      1  58.9    1   
Black Horse Pike Regional School District                 1      1  52.9    1   
Brooklawn Public School District                          1      1  55.1    1   
Camden City School District                               1      1   0.9    1   
Camden County Educational Services Commission             0      0   NaN  NaN   
Camden County Technical School District                   1      1  29.6    1   
Camden Prep Inc.                                          1      1   0.1    1   
Cherry Hill School District                               1      1  55.2    1   
Clementon Elementary School District                      1      1  33.7    1   
Collingswood Public School District                       1      1  60.1    1   
Eastern Camden County Regional School District            1      1  59.4    1   
Gibbsboro Elementary School District                      1      1  64.1    1   
Gloucester City Public School District                    1      1  61.8    1   
Gloucester Township Public Schools                        1      1  48.3    1   
Haddon Heights School District                            1      1  74.7    1   
Haddon Township School District                           1      1    80    1   
Haddonfield School District                               1      1  87.5    1   
Kipp: Cooper Norcross A New Jersey Nonprofit Co...        1      1   0.3    1   
Laurel Springs School District                            1      1  64.1    1   
Lawnside School Distric                                   1      1   1.3    1   
Lindenwold Public School District                         1      1   7.5    1   
Magnolia School District                                  1      1  50.1    1   
Mastery Schools Of Camden Inc.                            1      1   0.4    1   
Merchantville School District                             1      1  56.1    1   
Mt. Ephraim School District                               1      1  81.9    1   
Oaklyn Public School District                             1      1  76.9    1   
Pennsauken Township Board Of Education School D...        1      1   9.4    1   
Pine Hill School District                                 1      1  39.9    1   
Runnemede Public School District                          1      1    78    1   
Somerdale School District                                 1      1  39.7    1   
Sterling Regional School District                         1      1  56.1    1   
Stratford School District                                 1      1    59    1   
Voorhees Township School District                         1      1  50.6    1   
Waterford Township School District                        1      1  77.9    1   
Winslow Township School District                          1      1  19.1    1   
Woodlynne School District                                 1      1   2.3    1   

                                                   %Black_x                    \
                                                      count unique   top freq   
District Name                                                                   
Audubon Public School District                            1      1   3.3    1   
Barrington School District                                1      1   5.2    1   
Bellmawr Public School District                           1      1   4.1    1   
Berlin Borough School District                            1      1   7.1    1   


In [107]:
df3[['%White_y','%Black_y','%Hispanic_y','%Asian_y','District Name']].groupby('District Name').describe()

%White_y                    \
                                                      count   mean std    min   
District Name                                                                   
Audubon Public School District                          1.0   97.5 NaN   97.5   
Barrington School District                              1.0   96.7 NaN   96.7   
Bellmawr Public School District                         1.0   96.0 NaN   96.0   
Berlin Borough School District                          1.0  100.0 NaN  100.0   
Berlin Township School District                         1.0   94.6 NaN   94.6   
Black Horse Pike Regional School District               1.0   93.1 NaN   93.1   
Brooklawn Public School District                        1.0  100.0 NaN  100.0   
Camden City School District                             1.0   45.4 NaN   45.4   
Camden County Educational Services Commission           1.0    0.0 NaN    0.0   
Camden County Technical School District                 1.0   84.3 NaN   84.3   
Camden Prep Inc.                                        1.0   55.6 NaN   55.6   
Cherry Hill School District                             1.0   87.2 NaN   87.2   
Clementon Elementary School District                    1.0   96.0 NaN   96.0   
Collingswood Public School District                     1.0   91.4 NaN   91.4   
Eastern Camden County Regional School District          1.0   92.0 NaN   92.0   
Gibbsboro Elementary School District                    1.0  100.0 NaN  100.0   
Gloucester City Public School District                  1.0   97.7 NaN   97.7   
Gloucester Township Public Schools                      1.0   93.1 NaN   93.1   
Haddon Heights School District                          1.0   95.8 NaN   95.8   
Haddon Township School District                         1.0   98.3 NaN   98.3   
Haddonfield School District                             1.0   93.7 NaN   93.7   
Kipp: Cooper Norcross A New Jersey Nonprofit Co...      1.0   40.0 NaN   40.0   
Laurel Springs School District                          1.0  100.0 NaN  100.0   
Lawnside School Distric                                 1.0   42.3 NaN   42.3   
Lindenwold Public School District                       1.0   73.8 NaN   73.8   
Magnolia School District                                1.0   97.3 NaN   97.3   
Mastery Schools Of Camden Inc.                          1.0   60.5 NaN   60.5   
Merchantville School District                           1.0   89.4 NaN   89.4   
Mt. Ephraim School District                             1.0  100.0 NaN  100.0   
Oaklyn Public School District                           1.0  100.0 NaN  100.0   
Pennsauken Township Board Of Education School D...      1.0   81.1 NaN   81.1   
Pine Hill School District                               1.0   90.5 NaN   90.5   
Runnemede Public School District                        1.0   95.9 NaN   95.9   
Somerdale School District                               1.0   97.7 NaN   97.7   
Sterling Regional School District                       1.0   92.8 NaN   92.8   
Stratford School District                               1.0   97.8 NaN   97.8   
Voorhees Township School District                       1.0   97.5 NaN   97.5   
Waterford Township School District                      1.0   97.7 NaN   97.7   
Winslow Township School District                        1.0   80.1 NaN   80.1   
Woodlynne School District                               1.0   94.0 NaN   94.0   

                                                                         \
                                                      25%    50%    75%   
District Name                                                             
Audubon Public School District                       97.5   97.5   97.5   
Barrington School District                           96.7   96.7   96.7   
Bellmawr Public School District                      96.0   96.0   96.0   
Berlin Borough School District                      100.0  100.0  100.0   
Berlin Township School District           

In [117]:
df3[['enr','Total Enrollment']]

enr Total Enrollment
0    1444.0             1444
1     563.0              563
2    1166.0             1166
3     807.0              807
4     604.0              604
5    3478.0             3478
6     285.0              285
7    7343.0             7343
8       NaN              NaN
9    2245.0             2245
10  10469.0            10469
11    516.0              516
12   2200.0             2200
13   1926.0             1926
14    276.0              276
15   2220.0             2220
16   6368.0             6368
17   1775.0             1775
18    949.0              949
19   2737.0             2737
20   1514.0             1514
21   1971.0             1971
22   2645.0             2645
23    167.0              167
24    308.0              308
25   2926.0             2926
26    375.0              375
27    403.0              403
28    421.0              421
29    277.0              277
30   4649.0             4649
31   1807.0             1807
32    837.0              837
33    459.0              459
34    912.0              912
35    857.0              857
36   2914.0             2914
37    856.0              856
38   4606.0             4606
39    393.0              393

In [121]:
bins = [min(df3['enr']), 5000, max(df3['enr'])]
cats = ['small district', 'big district']
df3['weiCat'] = pd.cut(df3['enr'], bins=bins, labels=cats)
df3[['weiCat','enr']] # I divided these school districts as 'big district' and 'small district' by the total enrollment

weiCat      enr
0   small district   1444.0
1   small district    563.0
2   small district   1166.0
3   small district    807.0
4   small district    604.0
5   small district   3478.0
6   small district    285.0
7     big district   7343.0
8              NaN      NaN
9   small district   2245.0
10    big district  10469.0
11  small district    516.0
12  small district   2200.0
13  small district   1926.0
14  small district    276.0
15  small district   2220.0
16    big district   6368.0
17  small district   1775.0
18  small district    949.0
19  small district   2737.0
20  small district   1514.0
21  small district   1971.0
22  small district   2645.0
23             NaN    167.0
24  small district    308.0
25  small district   2926.0
26  small district    375.0
27  small district    403.0
28  small district    421.0
29  small district    277.0
30  small district   4649.0
31  small district   1807.0
32  small district    837.0
33  small district    459.0
34  small district    912.0
35  small district    857.0
36  small district   2914.0
37  small district    856.0
38  small district   4606.0
39  small district    393.0